# Projet 7 : Implémentez un modèle de scoring </span></center>

## <a id=''> Data Drift</a>

In [18]:
from jyquickhelper import add_notebook_menu
add_notebook_menu()

## <a id='1'>1. Importation des librairies</a>

In [19]:
import numpy as np
import pandas as pd
import math
import time
from evidently.report import Report
from evidently.metrics import DataDriftTable, DatasetDriftMetric
pd.options.display.max_columns = 200
np.random.seed(0)

## <a id="2">2. Importation des données </a>

In [20]:
train_df = pd.read_csv("data set/application_train.csv")

In [21]:
test_df= pd.read_csv("Data set/application_test.csv")

In [22]:
train_df.sample(2)

SK_ID_CURR  TARGET NAME_CONTRACT_TYPE CODE_GENDER FLAG_OWN_CAR  \
42962       149741       1         Cash loans           F            N   
227307      363290       0         Cash loans           M            N   

       FLAG_OWN_REALTY  CNT_CHILDREN  AMT_INCOME_TOTAL  AMT_CREDIT  \
42962                N             0          117000.0    417024.0   
227307               Y             0          450000.0    640080.0   

        AMT_ANNUITY  AMT_GOODS_PRICE  NAME_TYPE_SUITE      NAME_INCOME_TYPE  \
42962       20191.5         360000.0  Spouse, partner               Working   
227307      31261.5         450000.0    Unaccompanied  Commercial associate   

       NAME_EDUCATION_TYPE NAME_FAMILY_STATUS  NAME_HOUSING_TYPE  \
42962    Incomplete higher            Married  House / apartment   
227307    Higher education            Married  House / apartment   

        REGION_POPULATION_RELATIVE  DAYS_BIRTH  DAYS_EMPLOYED  \
42962                     0.020246      -21774          -2125   
227307                    0.046220      -18499          -2055   

        DAYS_REGISTRATION  DAYS_ID_PUBLISH  OWN_CAR_AGE  FLAG_MOBIL  \
42962             -4611.0            -4653          NaN           1   
227307            -3052.0            -2028          NaN           1   

        FLAG_EMP_PHONE  FLAG_WORK_PHONE  FLAG_CONT_MOBILE  FLAG_PHONE  \
42962                1                1                 1           1   
227307               1                0                 1           0   

        FLAG_EMAIL OCCUPATION_TYPE  CNT_FAM_MEMBERS  REGION_RATING_CLIENT  \
42962            0  Security staff              2.0                     3   
227307           0        Laborers              2.0                     1   

        REGION_RATING_CLIENT_W_CITY WEEKDAY_APPR_PROCESS_START  \
42962                             3                     FRIDAY   
227307                            1                    TUESDAY   

        HOUR_APPR_PROCESS_START  REG_REGION_NOT_LIVE_REGION  \
42962                        13                           0   
227307                       13                           0   

        REG_REGION_NOT_WORK_REGION  LIVE_REGION_NOT_WORK_REGION  \
42962                            0                            0   
227307                           0                            0   

        REG_CITY_NOT_LIVE_CITY  REG_CITY_NOT_WORK_CITY  \
42962                        0                       0   
227307                       0                       0   

        LIVE_CITY_NOT_WORK_CITY       ORGANIZATION_TYPE  EXT_SOURCE_1  \
42962                         0                Medicine      0.484936   
227307                        0  Business Entity Type 3      0.624574   

        EXT_SOURCE_2  EXT_SOURCE_3  APARTMENTS_AVG  BASEMENTAREA_AVG  \
42962       0.182710      0.145543             NaN               NaN   
227307      0.669053      0.680139          0.3763            0.4482   

        YEARS_BEGINEXPLUATATION_AVG  YEARS_BUILD_AVG  COMMONAREA_AVG  \
42962                           NaN              NaN             NaN   
227307                        0.995              NaN             NaN   

        ELEVATORS_AVG  ENTRANCES_AVG  FLOORSMAX_AVG  FLOORSMIN_AVG  \
42962             NaN            NaN            NaN            NaN   
227307           0.48         0.2069          0.625            NaN   

        LANDAREA_AVG  LIVINGAPARTMENTS_AVG  LIVINGAREA_AVG  \
42962            NaN                   NaN             NaN   
227307        0.0347                   NaN          0.4585   

        NONLIVINGAPARTMENTS_AVG  NONLIVINGAREA_AVG  APARTMENTS_MODE  \
42962                       NaN                NaN              NaN   
227307                      NaN              0.005           0.3834   

        BASEMENTAREA_MODE  YEARS_BEGINEXPLUATATION_MODE  YEARS_BUILD_MODE  \
42962                 NaN                           NaN               NaN   
227307             0.4651                         0.995               NaN   

     

In [23]:
test_df.sample(2)

SK_ID_CURR NAME_CONTRACT_TYPE CODE_GENDER FLAG_OWN_CAR FLAG_OWN_REALTY  \
42274      408986         Cash loans           F            N               N   
47415      446617         Cash loans           F            N               N   

       CNT_CHILDREN  AMT_INCOME_TOTAL  AMT_CREDIT  AMT_ANNUITY  \
42274             0          126000.0    270000.0      13783.5   
47415             0          112500.0    540000.0      17419.5   

       AMT_GOODS_PRICE NAME_TYPE_SUITE      NAME_INCOME_TYPE  \
42274         270000.0   Unaccompanied  Commercial associate   
47415         540000.0   Unaccompanied  Commercial associate   

                 NAME_EDUCATION_TYPE NAME_FAMILY_STATUS  NAME_HOUSING_TYPE  \
42274  Secondary / secondary special            Married  House / apartment   
47415               Higher education            Married  House / apartment   

       REGION_POPULATION_RELATIVE  DAYS_BIRTH  DAYS_EMPLOYED  \
42274                    0.010556      -10630          -1239   
47415                    0.010276      -18389           -314   

       DAYS_REGISTRATION  DAYS_ID_PUBLISH  OWN_CAR_AGE  FLAG_MOBIL  \
42274            -2183.0            -2511          NaN           1   
47415            -3923.0            -1895          NaN           1   

       FLAG_EMP_PHONE  FLAG_WORK_PHONE  FLAG_CONT_MOBILE  FLAG_PHONE  \
42274               1                0                 1           0   
47415               1                1                 1           0   

       FLAG_EMAIL OCCUPATION_TYPE  CNT_FAM_MEMBERS  REGION_RATING_CLIENT  \
42274           0             NaN              2.0                     3   
47415           0        Laborers              2.0                     2   

       REGION_RATING_CLIENT_W_CITY WEEKDAY_APPR_PROCESS_START  \
42274                            3                     MONDAY   
47415                            2                  WEDNESDAY   

       HOUR_APPR_PROCESS_START  REG_REGION_NOT_LIVE_REGION  \
42274                       11                           0   
47415                       10                           0   

       REG_REGION_NOT_WORK_REGION  LIVE_REGION_NOT_WORK_REGION  \
42274                           0                            0   
47415                           0                            0   

       REG_CITY_NOT_LIVE_CITY  REG_CITY_NOT_WORK_CITY  \
42274                       0                       1   
47415                       0                       0   

       LIVE_CITY_NOT_WORK_CITY       ORGANIZATION_TYPE  EXT_SOURCE_1  \
42274                        1                   Other      0.674564   
47415                        0  Business Entity Type 3           NaN   

       EXT_SOURCE_2  EXT_SOURCE_3  APARTMENTS_AVG  BASEMENTAREA_AVG  \
42274      0.371360      0.495666             NaN               NaN   
47415      0.492824      0.531686             NaN               NaN   

       YEARS_BEGINEXPLUATATION_AVG  YEARS_BUILD_AVG  COMMONAREA_AVG  \
42274                          NaN              NaN             NaN   
47415                          NaN              NaN             NaN   

       ELEVATORS_AVG  ENTRANCES_AVG  FLOORSMAX_AVG  FLOORSMIN_AVG  \
42274            NaN            NaN            NaN            NaN   
47415            0.0         0.2069         0.1667         0.2083   

       LANDAREA_AVG  LIVINGAPARTMENTS_AVG  LIVINGAREA_AVG  \
42274           NaN                   NaN             NaN   
47415        0.0752                   NaN          0.0762   

       NONLIVINGAPARTMENTS_AVG  NONLIVINGAREA_AVG  APARTMENTS_MODE  \
42274                      NaN                NaN              NaN   
47415                      NaN                NaN              NaN   

       BASEMENTAREA_MODE  YEARS_BEGINEXPLUATATION_MODE  YEARS_BUILD_MODE  \
42274                NaN                           NaN               NaN   
47415                NaN                           NaN               NaN   

       COMMONAREA_MODE  ELEVATORS_MODE  ENTRANCES_MODE 

In [24]:
def missing_general(dataframe, name):
    total_missing = dataframe.isnull().sum().sum()
    total_cells = dataframe.size
    percent_missing = (total_missing / total_cells) * 100
    print(f"{name} :")
    print(f"Nombre total de cellules manquantes : {total_missing}")
    print(f"Nombre de cellules manquantes en % : {percent_missing:.2f}%")
    print()

# Appel de la fonction pour chaque dataset
missing_general(train_df, "Le dataset train")
missing_general(test_df, "Le dataset test")

Le dataset train :
Nombre total de cellules manquantes : 9152465
Nombre de cellules manquantes en % : 24.40%

Le dataset test :
Nombre total de cellules manquantes : 1404419
Nombre de cellules manquantes en % : 23.81%



In [25]:
# Affichez les colonnes ayant au moins un NaN
cols_with_nan = train_df.columns[train_df.isna().any()]
print("Colonnes avec des valeurs NaN :")
print(cols_with_nan)

Colonnes avec des valeurs NaN :
Index(['AMT_ANNUITY', 'AMT_GOODS_PRICE', 'NAME_TYPE_SUITE', 'OWN_CAR_AGE',
       'OCCUPATION_TYPE', 'CNT_FAM_MEMBERS', 'EXT_SOURCE_1', 'EXT_SOURCE_2',
       'EXT_SOURCE_3', 'APARTMENTS_AVG', 'BASEMENTAREA_AVG',
       'YEARS_BEGINEXPLUATATION_AVG', 'YEARS_BUILD_AVG', 'COMMONAREA_AVG',
       'ELEVATORS_AVG', 'ENTRANCES_AVG', 'FLOORSMAX_AVG', 'FLOORSMIN_AVG',
       'LANDAREA_AVG', 'LIVINGAPARTMENTS_AVG', 'LIVINGAREA_AVG',
       'NONLIVINGAPARTMENTS_AVG', 'NONLIVINGAREA_AVG', 'APARTMENTS_MODE',
       'BASEMENTAREA_MODE', 'YEARS_BEGINEXPLUATATION_MODE', 'YEARS_BUILD_MODE',
       'COMMONAREA_MODE', 'ELEVATORS_MODE', 'ENTRANCES_MODE', 'FLOORSMAX_MODE',
       'FLOORSMIN_MODE', 'LANDAREA_MODE', 'LIVINGAPARTMENTS_MODE',
       'LIVINGAREA_MODE', 'NONLIVINGAPARTMENTS_MODE', 'NONLIVINGAREA_MODE',
       'APARTMENTS_MEDI', 'BASEMENTAREA_MEDI', 'YEARS_BEGINEXPLUATATION_MEDI',
       'YEARS_BUILD_MEDI', 'COMMONAREA_MEDI', 'ELEVATORS_MEDI',
       'ENTRANCES_ME

In [26]:
# Variables uniquement dans train_df mais pas dans test_df
variables_only_in_train = train_df.columns.difference(test_df.columns)

# Variables uniquement dans test_df mais pas dans train_df
variables_only_in_test = test_df.columns.difference(train_df.columns)

# Variables qui ne se trouvent pas dans les deux DataFrames
variables_only_in_both = variables_only_in_train.intersection(variables_only_in_test)

print("Variables uniquement dans les deux DataFrames :", variables_only_in_both)



Variables uniquement dans les deux DataFrames : Index([], dtype='object')


## <a id="3">3. Data Drift </a>

Le Data Drift est une variation des données du monde réel par rapport aux données utilisées pour tester et valider le modèle avant de le déployer en production. L’une des causes principales est la dimension temporelle.

Le data drift peut affecter les performances du modèle Machine Learning. Il existe différents types de drift. Il peut y avoir des changements dans la distribution cible, ou encore un *covariate drift* qui est un changement dans la distribution des données d'entrée (par exemple une variable aura une autre catégorie).

L'approche pour détecter le data drift consiste à utiliser des tests statistiques qui comparent la distribution des données de référence (reference data) et des données actuelles ou current data (données de production). Si la différence entre deux distributions est significative alors un drift s'est produit. 
Pour un dataset volumineux (avec > 1 000 observations dans l'ensemble de données de référence), la Distance de Wasserstein est utilisée pour les colonnes numériques (n_unique > 5), et pour les colonnes catégorielles ou numériques (avec n_unique <= 5) c'est la Divergence de Jensen--Shannon qui est appliquée.

In [27]:
ref = train_df.drop(['TARGET'],axis=1).iloc[:48744,:]
cur = test_df

In [28]:
data_drift_dataset_report = Report(metrics=[DatasetDriftMetric(), DataDriftTable()])

data_drift_dataset_report.run(reference_data=ref, current_data=cur)

In [29]:
data_drift_dataset_report.show(mode='inline')

On constate donc qu'il n'y a pas de data drift entre nos données de référence (données d'entrainement) et nos données actuelles (données de test), bien qu'un léger drift ait été détecté dans 10 de nos colonnes.